## הגדרות ומקדים

### ספריות

In [1]:
import os
import sys
import fiona
import pandas as pd
import geopandas as gpd
from openpyxl import load_workbook

In [2]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.float_format', lambda x: '%.3f' % x)

### העלת משתנים להרצת הקוד

In [3]:
path = os.getcwd()

software_root_folder = os.path.dirname(path)

software_folder_location = r'{}\current'.format(software_root_folder)

df_inputs_outputs = pd.read_excel(r'{}\inputs_outputs.xlsx'.format(software_folder_location))

forecast_version_folder_location=df_inputs_outputs['location'][1]

output_location=df_inputs_outputs['location'][2]

sys.path.append(software_root_folder)

current_df_inputs_outputs = pd.read_excel(r'{}\inputs_outputs.xlsx'.format(software_folder_location))

TAZ_V4_date = '240408'

## פונקציות

### פונקציות גלובליות

In [4]:
from global_functions import up_load_shp, up_load_df, drop_geo, make_point, up_load_gdb, change_cols_names

## להריץ תלמידים

In [5]:
%run "students_current_year.ipynb"

## להעלות שכבות

In [6]:
path=r'{}\background_files\EMP_KIBOLET.gdb'.format(software_folder_location)

EMP_kibolet=up_load_gdb(path,'EMP_kibolet')

In [7]:
EMP_kibolet=EMP_kibolet.fillna(0)

EMP_kibolet['emp_without_palestin']=EMP_kibolet['kayim_emp']-EMP_kibolet['Palestinians']

emp_without_palestin_not_okev=EMP_kibolet['emp_without_palestin'].sum().item()

emp_Education=taz.query('main_secto!="Palestinian"')['emp_Education'].sum().item()

## הוספת סטודנטים לאוכלוסיה ולהתפלגות גילים

In [8]:
student_dorms=up_load_shp(r'{}\background_files\student_dorms.shp'.format(software_folder_location))

In [9]:
#העלה של נתוני אנשים התפלגות גילים שנוצר לפני הקוד הזה
path=r'{}\Intermediates'.format(software_folder_location)
taz_with_pop=up_load_df(path,'taz_with_pop_info')

In [10]:
col_needed=['Taz_num','aprt_20',
 'pop',
 'pop_0',
 'pop_10',
 'pop_15',
 'pop_20',
 'pop_25',
 'pop_30',
 'pop_35',
 'pop_40',
 'pop_45',
 'pop_5',
 'pop_50',
 'pop_55',
 'pop_60',
 'pop_65',
 'pop_70',
 'pop_75up', 'hh_size']

In [11]:
taz=taz.merge(taz_with_pop[col_needed],on='Taz_num',how='left')

In [12]:
taz=taz.set_index('Taz_num')

In [13]:
taz['student_dorms']=gpd.sjoin(taz[['geometry']].reset_index(),student_dorms)[['Taz_num','student_nu']].pivot_table(index='Taz_num',aggfunc='sum')


In [14]:

taz=taz.fillna(0)

taz['pop_without_dorms_yeshiva']=taz['pop']

taz['pop']=taz['pop']+taz['student_dorms']

taz['pop_20_just_from_aprt']=taz['pop_20']

taz['pop_25_just_from_aprt']=taz['pop_25']

taz['pop_20']=taz['pop_20']+taz['student_dorms']*0.6

taz['pop_25']=taz['pop_25']+taz['student_dorms']*0.4

In [15]:
col=['pop_0',
 'pop_10',
 'pop_15',
 'pop_20',
 'pop_25',
 'pop_30',
 'pop_35',
 'pop_40',
 'pop_45',
 'pop_5',
 'pop_50',
 'pop_55',
 'pop_60',
 'pop_65',
 'pop_70',
 'pop_75up',]

taz['pop_check']=round(taz[col].sum(axis=1)-taz['pop'])

taz.loc[taz['main_secto']!="Palestinian"].loc[taz['pop_check']!=0]

Empty GeoDataFrame
Columns: [Taz_name, jeru_metro, in_jerusal, main_secto, SCHN_NAME, ENG_NAME_n, zonetype, Muni_Heb, Sug_Muni, CR_PNIM, highBusine, SCHOOLDIST, Urban, EIProp, poly_puma, F3, F2, F1, agri, Indus, Com_hotel, Business, Public, commuting, ieold, IEProp, perScaled, FreeBuffer, PaidBuffer, Rest_EmpBu, searchtime, walktime, cost, Agg_taz_nu, area, CITYCODE1, CITYCODE2, CITYCODE3, CITYCODE4, codeseq, codeseqCon, county, majunivenr, parktot, superZone, Taz1, slope, REGION, yosh, jerusalem_, geometry, SEA1, SEA2, SEA3, UOA1, UOA2, UOA3, ARA1, ARA2, ARA3, student_chardi_not_gov, student_arab_not_gov, TOA1, TOA2, TOA3, sector_for_chinuc, student, Univ_AR, Univ_SE, Univ_UO, emp_uni, univ, UNIVENRORTHFEMALE, UNIVENRORTHMALE, yeshiva_dorms_pop_15, yeshiva_dorms_pop_20, yeshiva_dorms_pop_25, yeshiva_dorms_pop_sum, emp_from_Yeshiva_student, Yeshiva, Seminar_dorms_pop_15, Seminar_dorms_pop_20, Seminar_dorms_pop_25, Seminar_dorms_pop_sum, emp_from_Seminar_student, Seminar, kollim_demand, add_from_kollim_demand, student_yeshiva_and_kollim, UO_Hi_Ed, emp_UO_Hi_Ed, jew, emp_from_student, emp_Education, aprt_20, pop, pop_0, pop_10, pop_15, pop_20, ...]
Index: []

## הוספת תלמידי ישיבה (באזורים חרדיים) אל כמות אוכלוסיה,התפלגות גילים 

In [16]:
taz['pop_15_just_from_aprt']=taz['pop_15']

In [17]:

taz.loc[taz['main_secto']=="U_Orthodox",'pop']=taz['pop']+taz['yeshiva_dorms_pop_sum']

taz.loc[taz['main_secto']=="U_Orthodox",'pop_15']=taz['pop_15']+taz['yeshiva_dorms_pop_15']

taz.loc[taz['main_secto']=="U_Orthodox",'pop_20']=taz['pop_20']+taz['yeshiva_dorms_pop_20']

taz.loc[taz['main_secto']=="U_Orthodox",'pop_25']=taz['pop_25']+taz['yeshiva_dorms_pop_25']

In [18]:
col=['pop_0',
 'pop_10',
 'pop_15',
 'pop_20',
 'pop_25',
 'pop_30',
 'pop_35',
 'pop_40',
 'pop_45',
 'pop_5',
 'pop_50',
 'pop_55',
 'pop_60',
 'pop_65',
 'pop_70',
 'pop_75up',]

taz['pop_check']=round(taz[col].sum(axis=1)-taz['pop'])

taz.loc[taz['main_secto']!="Palestinian"].loc[taz['pop_check']!=0]

Empty GeoDataFrame
Columns: [Taz_name, jeru_metro, in_jerusal, main_secto, SCHN_NAME, ENG_NAME_n, zonetype, Muni_Heb, Sug_Muni, CR_PNIM, highBusine, SCHOOLDIST, Urban, EIProp, poly_puma, F3, F2, F1, agri, Indus, Com_hotel, Business, Public, commuting, ieold, IEProp, perScaled, FreeBuffer, PaidBuffer, Rest_EmpBu, searchtime, walktime, cost, Agg_taz_nu, area, CITYCODE1, CITYCODE2, CITYCODE3, CITYCODE4, codeseq, codeseqCon, county, majunivenr, parktot, superZone, Taz1, slope, REGION, yosh, jerusalem_, geometry, SEA1, SEA2, SEA3, UOA1, UOA2, UOA3, ARA1, ARA2, ARA3, student_chardi_not_gov, student_arab_not_gov, TOA1, TOA2, TOA3, sector_for_chinuc, student, Univ_AR, Univ_SE, Univ_UO, emp_uni, univ, UNIVENRORTHFEMALE, UNIVENRORTHMALE, yeshiva_dorms_pop_15, yeshiva_dorms_pop_20, yeshiva_dorms_pop_25, yeshiva_dorms_pop_sum, emp_from_Yeshiva_student, Yeshiva, Seminar_dorms_pop_15, Seminar_dorms_pop_20, Seminar_dorms_pop_25, Seminar_dorms_pop_sum, emp_from_Seminar_student, Seminar, kollim_demand, add_from_kollim_demand, student_yeshiva_and_kollim, UO_Hi_Ed, emp_UO_Hi_Ed, jew, emp_from_student, emp_Education, aprt_20, pop, pop_0, pop_10, pop_15, pop_20, ...]
Index: []

## כימות מועסקים במרחב צתאל

In [19]:
pre_woman=0.5

pre_man=1-pre_woman

In [20]:
work_age=[ 'pop_25',
 'pop_30',
 'pop_35',
 'pop_40',
 'pop_45',
 'pop_50',
 'pop_55',
 'pop_60']

under_work_age=[ 'pop_15', 'pop_20']

over_work_age=[ 'pop_65', 'pop_70', 'pop_75up']

In [21]:
taz['work_age']=taz[work_age].sum(axis=1)

taz['under_work_age']=taz[under_work_age].sum(axis=1)

taz['over_work_age']=taz[over_work_age].sum(axis=1)

In [22]:
sector='U_Orthodox'

taz.loc[taz['main_secto']==sector,'pop_emp']=taz['work_age']*pre_woman*0.75+taz['work_age']*pre_man*0.55
taz.loc[taz['main_secto']==sector,'pop_emp']=taz['pop_emp']+taz['under_work_age']*pre_woman*0.07+taz['under_work_age']*pre_man*0.09
taz.loc[taz['main_secto']==sector,'pop_emp']=taz['pop_emp']+taz['over_work_age']*pre_woman*0.05+taz['over_work_age']*pre_man*0.09

sector='Jewish'

taz.loc[taz['main_secto']==sector,'pop_emp']=taz['work_age']*pre_woman*0.9+taz['work_age']*pre_man*0.92
taz.loc[taz['main_secto']==sector,'pop_emp']=taz['pop_emp']+taz['under_work_age']*pre_woman*0.20+taz['under_work_age']*pre_man*0.15
taz.loc[taz['main_secto']==sector,'pop_emp']=taz['pop_emp']+taz['over_work_age']*pre_woman*0.2+taz['over_work_age']*pre_man*0.15

sector='Arab'

taz.loc[taz['main_secto']==sector,'pop_emp']=taz['work_age']*pre_woman*0.25+taz['work_age']*pre_man*0.7
taz.loc[taz['main_secto']==sector,'pop_emp']=taz['pop_emp']+taz['under_work_age']*pre_woman*0.2+taz['under_work_age']*pre_man*0.15
taz.loc[taz['main_secto']==sector,'pop_emp']=taz['pop_emp']+taz['over_work_age']*pre_woman*0.05+taz['over_work_age']*pre_man*0.09

sector='arabs_behined_seperation_wall'

taz.loc[taz['main_secto']==sector,'pop_emp']=taz['work_age']*pre_woman*0.25+taz['work_age']*pre_man*0.7
taz.loc[taz['main_secto']==sector,'pop_emp']=taz['pop_emp']+taz['under_work_age']*pre_woman*0.2+taz['under_work_age']*pre_man*0.15
taz.loc[taz['main_secto']==sector,'pop_emp']=taz['pop_emp']+taz['over_work_age']*pre_woman*0.05+taz['over_work_age']*pre_man*0.09


## חישוב אבטלה

In [23]:
taz['pop_emp_employed']=0

taz.loc[taz['main_secto']=="U_Orthodox",'pop_emp_employed']=taz['pop_emp']*0.97

taz.loc[taz['main_secto']=="Jewish",'pop_emp_employed']=taz['pop_emp']*0.98

taz.loc[taz['jew']==0,'pop_emp_employed']=taz['pop_emp']*0.95

## חישוב יוממות

In [24]:
taz['pop_emp_employed_out_of_jtmt_area']=taz['pop_emp_employed']*taz['commuting']

emp_left_jtmt_area=taz['pop_emp_employed_out_of_jtmt_area'].sum().item()

round(emp_left_jtmt_area,-3)

94000.0

In [25]:
emp_from_jtmt_area=taz['pop_emp_employed'].sum().item()-emp_left_jtmt_area

emp_in_jtmt_area=emp_from_jtmt_area*1.07 #יוממות פנימה מחוץ למרחב

round(emp_in_jtmt_area,-3)

510000.0

In [26]:
emp_in_jtmt_area_without_mobile=emp_in_jtmt_area*0.95 #הפחחת עובדים ניידים

round(emp_in_jtmt_area_without_mobile,-3)

484000.0

In [27]:
emp_okev=emp_in_jtmt_area_without_mobile-emp_Education-emp_without_palestin_not_okev

## פיזור עוקב

In [28]:
EMP_kibolet['geometry_buff']=EMP_kibolet.buffer(250)

EMP_buffer=EMP_kibolet.set_geometry('geometry_buff').query('kayim_emp>0')

EMP_buffer=EMP_buffer.dissolve()[['geometry_buff']]

taz['taz_area']=taz.area

In [29]:
emp_buffer_taz=gpd.overlay(EMP_buffer,taz.reset_index())

emp_buffer_taz['emp_samll_area']=emp_buffer_taz.area

emp_buffer_taz['emp_pre_from_taz']=emp_buffer_taz['emp_samll_area']/emp_buffer_taz['taz_area']

In [30]:
taz_num_no_need_okev=emp_buffer_taz.loc[emp_buffer_taz['emp_pre_from_taz']>0.4].Taz_num.to_list()

In [31]:
taz['okev']=0
taz.loc[(~taz.index.isin(taz_num_no_need_okev))&(taz['pop']>0)&(taz['main_secto']!="Palestinia"),'okev']=1

taz.loc[taz['main_secto']=="arabs_behined_seperation_wall",'okev']=1

In [32]:
city_muni=['מודיעין עילית','בית שמש','ירושלים','מודיעין - מכבים - רעות']

## מקדם עוקב

In [33]:
okev_level=0.15

arab_city=taz.query('jew==0 & okev==1')['aprt_20'].sum().item()

arab_sub=0

ou_sub=taz.query('main_secto=="U_Orthodox" & ~Muni_Heb.isin(@city_muni) & okev==1')['aprt_20'].sum().item()

In [34]:
ou_city=taz.query('main_secto=="U_Orthodox" & Muni_Heb.isin(@city_muni) & okev==1')['aprt_20'].sum().item()

general_city=taz.query('main_secto=="Jewish" & Muni_Heb.isin(@city_muni) & okev==1')['aprt_20'].sum().item()

general_sub=taz.query('main_secto=="Jewish" & ~Muni_Heb.isin(@city_muni) & okev==1')['aprt_20'].sum().item()

base_okev_factor=(emp_okev-(okev_level*general_city-okev_level*(ou_sub+arab_city)-2*okev_level*arab_sub))/(general_sub+general_city+ou_city+ou_sub+arab_city+arab_sub)

base_okev_factor=round(base_okev_factor,3)

In [35]:
data = [['Jewish', base_okev_factor,base_okev_factor+okev_level],['arab', base_okev_factor-okev_level,base_okev_factor], ['U_Orthodox',base_okev_factor-2*okev_level,base_okev_factor-okev_level]]
 
# Create the pandas DataFrame
df = pd.DataFrame(data, columns=['sector', 'sub','city'])
okev_factor=df.set_index('sector')
okev_factor.to_excel(r'{}\Intermediates\okev_factor.xlsx'.format(software_folder_location))

In [36]:
taz['emp_okev']=0

taz.loc[(taz['jew']==0)&(taz['okev']==1),'emp_okev']=taz['aprt_20']*okev_factor.loc['arab','city']

taz.loc[(taz['main_secto']=="U_Orthodox")&(~taz['Muni_Heb'].isin(city_muni))&(taz['okev']==1),'emp_okev']=taz['aprt_20']*okev_factor.loc['U_Orthodox','sub']

taz.loc[(taz['main_secto']=="U_Orthodox")&(taz['Muni_Heb'].isin(city_muni))&(taz['okev']==1),'emp_okev']=taz['aprt_20']*okev_factor.loc['U_Orthodox','city']

taz.loc[(taz['main_secto']=="Jewish")&(taz['Muni_Heb'].isin(city_muni))&(taz['okev']==1),'emp_okev']=taz['aprt_20']*okev_factor.loc['Jewish','city']

taz.loc[(taz['main_secto']=="Jewish")&(~taz['Muni_Heb'].isin(city_muni))&(taz['okev']==1),'emp_okev']=taz['aprt_20']*okev_factor.loc['Jewish','sub']

taz.emp_okev.sum().item()-emp_okev

-1640.507337908377

## פיצול שכבת לא עוקב לאזורי תנועה

In [37]:
EMP_kibolet['emp_area']=EMP_kibolet.area

EMP_kibolet['ID']=EMP_kibolet.index

EMP_kibolet_by_taz=gpd.overlay(taz.reset_index()[['Taz_num','taz_area','geometry']],EMP_kibolet)

EMP_kibolet_by_taz['small_area']=EMP_kibolet_by_taz.area

C:\Users\gidon\AppData\Local\Temp\ipykernel_144084\1806380584.py:5: UserWarning: `keep_geom_type=True` in overlay resulted in 279 dropped geometries of different geometry types than df1 has. Set `keep_geom_type=False` to retain all geometries
  EMP_kibolet_by_taz=gpd.overlay(taz.reset_index()[['Taz_num','taz_area','geometry']],EMP_kibolet)


In [38]:
EMP_kibolet_by_taz['pre_small_area_emp']=EMP_kibolet_by_taz['small_area']/EMP_kibolet_by_taz['emp_area']

EMP_kibolet_by_taz['pre_small_area_taz']=EMP_kibolet_by_taz['small_area']/EMP_kibolet_by_taz['taz_area']

EMP_kibolet_by_taz=EMP_kibolet_by_taz.query('(pre_small_area_taz >0.7) | (pre_small_area_emp >0.1)').drop(columns='geometry_buff')

EMP_kibolet_by_taz=EMP_kibolet_by_taz.set_index('ID')


In [39]:
EMP_kibolet_by_taz['id_area_for_pre']=EMP_kibolet_by_taz.reset_index().groupby(by='ID')['small_area'].sum()

EMP_kibolet_by_taz['prec_from_id']=EMP_kibolet_by_taz['small_area']/EMP_kibolet_by_taz['id_area_for_pre']

EMP_kibolet_by_taz['emp_without_palestin_in_taz']=EMP_kibolet_by_taz['emp_without_palestin']*EMP_kibolet_by_taz['prec_from_id']

taz['emp_not_okev']=drop_geo(EMP_kibolet_by_taz).pivot_table(index='Taz_num',aggfunc='sum')[['emp_without_palestin_in_taz']]



In [40]:
taz=taz.fillna(0)

taz['total_emp']=taz['emp_not_okev']+taz['emp_okev']+taz['emp_Education']

taz.query('main_secto!="Palestinian"')['total_emp'].sum()-emp_in_jtmt_area_without_mobile

-1640.5073379084934

## התפלגות ענפי תעסוקה

In [41]:
for i in col:
    taz['{}'.format(i)]=taz['{}'.format(i)]*(taz['emp_not_okev']+taz['emp_okev'])

In [42]:
taz['check_emp_sum']=taz[col].sum(axis=1)-(taz['emp_not_okev']+taz['emp_okev'])

taz.query('check_emp_sum>10 |check_emp_sum<-10')

Taz_name  jeru_metro in_jerusal  \
Taz_num                                                            
6006.000            נוה יעקב - מרכז מסחרי       1.000        yes   
6007.000                   נוה יעקב תחתון       1.000        yes   
5807.000                 רמות - בריכת מים       1.000        yes   
5802.000                 רמות - הדף היומי       1.000        yes   
6401.000        מחנה פליטים שועפאת - מזרח       1.000        yes   
5703.000              רמות - גן טכנולוגיה       1.000        yes   
5104.000                          סנהדריה       1.000        yes   
5213.000                       שיכון חב_ד       1.000        yes   
5103.000                      שמואל הנביא       1.000        yes   
5505.000               הר נוף - צפון מערב       1.000        yes   
101.000                        גאולה מזרח       1.000        yes   
903.000                    מקור ברוך מערב       1.000        yes   
111.000                          ככר השבת       1.000        yes   
1206.000                         א סוואנה       1.000        yes   
902.000                    מקור ברוך דרום       1.000        yes   
5502.000                    הר נוף - דרום       1.000        yes   
5504.000               הר נוף - דרום מערב       1.000        yes   
1201.000                            א טור       1.000        yes   
608.000                     קמפוס גבעת רם       1.000        yes   
4906.000                    בית הכרם מרכז       1.000        yes   
2.000                           נחלת שבעה       1.000        yes   
805.000                          שערי חסד       1.000        yes   
507.000                      קרית וולפסון       1.000        yes   
409.000                             ממילא       1.000        yes   
2303.000                 ג'בל בטן אל הווא       1.000        yes   
4501.000            קרית יובל-רח' אנילביץ       1.000        yes   
4502.000                   קרית יובל מזרח       1.000        yes   
3804.000                            קטמון       1.000        yes   
2101.000                  ג'בל מוכבר מערב       1.000        yes   
3701.000              המושבה היוונית מערב       1.000        yes   
4505.000            קרית יובל-מרכז קהילתי       1.000        yes   
4605.000                        קרית מנחם       1.000        yes   
4607.000                       עיר גנים א       1.000        yes   
3908.000                        מקור חיים       1.000        yes   
4604.000                       עיר גנים ב       1.000        yes   
4201.000                           גונן ח       1.000        yes   
4202.000                           גונן ט       1.000        yes   
3112.000                         רמות רחל       1.000        yes   
3201.000           תלפז - רח' אבשלום חביב       1.000        yes   
3705.000                               פת       1.000        yes   
3204.000                    תיכון סליסברג       1.000        yes   
3202.000              תלפז - רח' דב גרונר       1.000        yes   
3605.000                    בית צפפה צפון       1.000        yes   
3203.000             תלפז - רח' משה ברזני       1.000        yes   
2505.000                         צור באהר       1.000        yes   
3401.000                 גילה א - אפרסמון       1.000        yes   
6002.000                    נוה יעקב דרום       1.000        yes   
6005.000             נוה יעקב - צפון מערב       1.000        yes   
2404.000                        אום ליסון       1.000        yes   
6303.000        פסגת זאב מזרח - דרום מזרח       1.000        yes   
6402.000             שועפאת - אזור תעסוקה       1.000        yes   
5107.000           רמת אשכול - מרכז מסחרי       1.000        yes   
209.000             שער מנדלבאום - מלונות       1.000        yes   
206.000                           שער שכם       1.000        yes   
201.000         משרד המשפטים מזרח ירושלים       1.000        yes   
3402.000                 גילה - בריכת מים       1.000        yes   
3004.000              את תלפיות-רח' האומן       1.000        yes   
3702.000             

## הוספת סטודנטים אל כמות משקי בית

In [43]:
taz=taz.fillna(0)

taz['hh']=taz['aprt_20']+taz['student_dorms']/1.5

## הוספת תלמידי ישיבה (באזורים לא חרדיים) אל כמות אוכלוסיה,התפלגות גילים ומשקי בית (לכלל תלמידי הישיבה)

In [44]:
taz['hh']=taz['hh']+taz['yeshiva_dorms_pop_sum']

In [45]:
taz.loc[taz['main_secto']!="U_Orthodox",'pop']=taz['pop']+taz['yeshiva_dorms_pop_sum']

taz.loc[taz['main_secto']!="U_Orthodox",'pop_15']=taz['pop_15']+taz['yeshiva_dorms_pop_15']

taz.loc[taz['main_secto']!="U_Orthodox",'pop_20']=taz['pop_20']+taz['yeshiva_dorms_pop_20']

taz.loc[taz['main_secto']!="U_Orthodox",'pop_25']=taz['pop_25']+taz['yeshiva_dorms_pop_25']

## הוספת אוכלוסיה פלסטינאית

In [46]:
path=r'{}\background_files'.format(software_folder_location)
taz_demo_pls_2020=up_load_df(path,'taz_demo_pls_2020_and_pre_growth_till_2050')[['Taz_num','pop_2020']].set_index('Taz_num')

In [47]:

taz.loc[taz['main_secto']=='Palestinian','pop']=taz['pop']+taz_demo_pls_2020['pop_2020']

In [48]:
save_taz_path=r'{}\Intermediates'.format(software_folder_location)
taz.to_excel(r'{}\taz_before_add_geo.xlsx'.format(save_taz_path))
